In [8]:
%matplotlib qt

import numpy as np

from numpy.random import rand

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
import scipy as sp

In [9]:
#initialize conditions
alpha = 0.0002 #K^-1
beta = 0.001 
S0 = 10     #ppt
k = 3e-9      #s^-1
lamda = 3e-11    #s^-1
dT=10 #K
p0=1026 #kgm^-3

dt=3600*24*30*12


T1=35+273.15 #K
T2=0+273.15


S1=35 #g/kg
S01=35
S2=25
S02=25
q=k*(alpha*(T1-T2)-beta*(S1-S2))
dS0=np.array([S1,S2,T1,T2,q])
print(dS0)

[ 3.5000e+01  2.5000e+01  3.0815e+02  2.7315e+02 -9.0000e-12]


In [10]:
#define conservation equations
def StommelODE(t,dS0):
    global S01, S02, lamda #makes use of the S01,S02 outside of the function
    S1=dS0[0] 
    S2=dS0[1] 
    T1=dS0[2] 
    T2=dS0[3]
    q=dS0[4]
    
    H1=-lamda*(S1-S01) 
    H2=-lamda*(S2-S02)
    
    dT1dt=-1*np.abs(q)*(T2-T1)
    dT2dt=np.abs(q)*(T1-T2)
    dS1dt=H1+np.abs(q)*(S2-S1)
    dS2dt=H2+np.abs(q)*(S1-S2)
    dqdt=-k*beta*(-2*np.abs(q)*(S1-S2)+2*H1)
    return np.array([dS1dt,dS2dt,dT1dt,dT2dt,dqdt])


In [11]:
#solve numerically using Runge-Kutta
alpha = 0.0002 #K^-1
beta = 0.001 
S0 = 10     #ppt
k = 3e-9      #s^-1
lamda = 3e-11    #s^-1
dT=10 #K
p0=1026 #kgm^-3

dt=3600*24*30*12


T1=35+273.15 #K
T2=0+273.15


S1=35 #g/kg
S01=35
S2=25
S02=25
q=k*(alpha*(T1-T2)-beta*(S1-S2))
dS0 = np.array([S1,S2,T1,T2,q])
dS  = np.copy(dS0)
print(dS0)
t = 0
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Stommelq', artist='Matplotlib',comment='')
writer = FFMpegWriter(fps=60, metadata=metadata)
fig = plt.figure()
year = 3600*24*365
with writer.saving(fig, "animation.mp4", dpi=200):

    while (t<1000*year):
        S1= dS[0]
        S2= dS[1]
        T1= dS[2]
        T2= dS[3]
        q = dS[4]

        f1 = StommelODE(t       ,dS          )
        f2 = StommelODE(t+dt/2.0,dS+f1*dt/2.0)
        f3 = StommelODE(t+dt/2.0,dS+f2*dt/2.0)
        f4 = StommelODE(t+dt    ,dS+f3*dt    )

        dS = dS + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
        t = t + year 
        print("{}...".format(t//year),end="")
        plt.clf()
        parameters = ['S1', 'S2']
        ps = [S1,S2]

        plt.subplot(2,1,1)

        #This will create the bar graph for poulation
        sal = plt.bar(parameters,ps,color=["red","blue"])
        plt.ylabel('Salinity[g/kg]')
        plt.xticks(('S1', 'S2'))
        plt.yticks(np.arange(0, 40, 10))
        plt.ylim(0,40)
        #The below code will create the second plot.

        parameters2 = ['q']
        ps2 = [-q]




        plt.subplot(2,1,2)
        #This will create the bar graph for gdp i.e gdppercapita divided by population.
        q =plt.bar(parameters2, ps2, color=["black"])
        plt.ylabel('flow strength [s^-1]')
        plt.xticks(('q'))
        plt.yticks(np.arange(0, 10*10**-12, (10*10**-12)/10))
        plt.ylim(0,10*10**-12)
        plt.show()
        plt.draw()
        if (t // year) % 20 == 0:
            writer.grab_frame()
        plt.pause(0.1)

[ 3.5000e+01  2.5000e+01  3.0815e+02  2.7315e+02 -9.0000e-12]
1...2...3...4...5...6...7...8...9...10...11...12...13...14...15...16...17...18...19...20...21...22...23...24...25...26...27...28...29...30...31...32...33...34...35...36...37...38...39...40...41...42...43...44...45...46...47...48...49...50...51...52...53...54...55...56...57...58...59...60...61...62...63...64...65...66...67...68...69...70...71...72...73...74...75...76...77...78...79...80...81...82...83...84...85...86...87...88...89...90...91...92...93...94...95...96...97...98...99...100...101...102...103...104...105...106...107...108...109...110...111...112...113...114...115...116...117...118...119...120...121...122...123...124...125...126...127...128...129...130...131...132...133...134...135...136...137...138...139...140...141...142...143...144...145...146...147...148...149...150...151...152...153...154...155...156...157...158...159...160...161...162...163...164...165...166...167...168...169...170...171...172...173...174...17

UNSTABLE CASE:
Now we add a forcing into the second box. This could be the result of a meteroite impact or sudden climate change on Earth. We do this by increasing the magnitude of the H variable associated with the high latitude box significantly. I did this to try to model what may have occurred in the Younger Dryas.  



In [12]:
def StommelODE1(t,dS0):
    global S01, S02, lamda #makes use of the S01,S02 outside of the function
    S1=dS0[0]
    S2=dS0[1]
    T1=dS0[2]
    T2=dS0[3]
    q=dS0[4]
    H1=-lamda*(S1-S01)
    H2=-3000*lamda*(S2-S02)
    
    dT1dt=-1*np.abs(q)*(T2-T1)
    dT2dt=np.abs(q)*(T1-T2)
    dS1dt=H1+np.abs(q)*(S2-S1)
    dS2dt=H2+np.abs(q)*(S1-S2)
    dqdt=-k*beta*(-2*np.abs(q)*(S1-S2)+2*H1)
    return np.array([dS1dt,dS2dt,dT1dt,dT2dt,dqdt])


In [13]:
alpha = 0.0002 #K^-1
beta = 0.001 
S0 = 10     #ppt
k = 3e-9      #s^-1
lamda = 3e-11    #s^-1
dT=10 #K
p0=1026 #kgm^-3

dt=3600*24*30*12


T1=35+273.15 #K
T2=0+273.15


S1=35 #g/kg
S01=35
S2=25
S02=25
q=k*(alpha*(T1-T2)-beta*(S1-S2))
dS0 = np.array([S1,S2,T1,T2,q])
dS  = np.copy(dS0)
print(dS0)
t = 0
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Stommelq', artist='Matplotlib',comment='')
writer = FFMpegWriter(fps=60, metadata=metadata)
fig = plt.figure()
year = 3600*24*365
with writer.saving(fig, "Animation2.mp4", dpi=200):

    while (t<750*year): #shorter time scale this time because of rapid change
        S1= dS[0]
        S2= dS[1]
        T1= dS[2]
        T2= dS[3]
        q = dS[4]

        f1 = StommelODE1(t       ,dS          )
        f2 = StommelODE1(t+dt/2.0,dS+f1*dt/2.0)
        f3 = StommelODE1(t+dt/2.0,dS+f2*dt/2.0)
        f4 = StommelODE1(t+dt    ,dS+f3*dt    )

        dS = dS + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
        t = t + year 
        print("{}...".format(t//year),end="")
        plt.clf()
        
        parameters = ['S1', 'S2']
        ps = [S1,S2]

        plt.subplot(2,1,1)
        sal = plt.bar(parameters,ps,color=["red","blue"])
        plt.ylabel('Salinity[g/kg]')
        plt.xticks(('S1', 'S2'))
        plt.yticks(np.arange(0, 40, 10))
        plt.ylim(0,40)
        
        parameters2 = ['q']
        ps2 = [-q]




        plt.subplot(2,1,2)
        q =plt.bar(parameters2, ps2, color=["black"])
        plt.ylabel('flow strength [s^-1]')
        plt.xticks(('q'))
        plt.yticks(np.arange(0, 10*10**-12, (10*10**-12)/10))
        plt.ylim(0,10*10**-12)
        plt.show()
        plt.draw()
        if (t // year) % 20 == 0:
            writer.grab_frame()
        plt.pause(0.1)

[ 3.5000e+01  2.5000e+01  3.0815e+02  2.7315e+02 -9.0000e-12]
1...2...3...4...5...6...7...8...9...10...11...12...13...14...15...16...17...18...19...20...21...22...23...24...25...26...27...28...29...30...31...32...33...34...35...36...37...38...39...40...41...42...43...44...45...46...47...48...49...50...51...52...53...54...55...56...57...58...59...60...61...62...63...64...65...66...67...68...69...70...71...72...73...74...75...76...77...78...79...80...81...82...83...84...85...86...87...88...89...90...91...92...93...94...95...96...97...98...99...100...101...102...103...104...105...106...107...108...109...110...111...112...113...114...115...116...117...118...119...120...121...122...123...124...125...126...127...128...129...130...131...132...133...134...135...136...137...138...139...140...141...142...143...144...145...146...147...148...149...150...151...152...153...154...155...156...157...158...159...160...161...162...163...164...165...166...167...168...169...170...171...172...173...174...17